In [1]:
from mpl_toolkits.basemap import Basemap  # import Basemap matplotlib toolkit
import numpy as np
import matplotlib.pyplot as plt
import pygrib # import pygrib interface to grib_api
import pandas as pd
import os
import sys
import math
import folium
import csv 
import time

year="2018"
month="01"
day="01"

start = time.time()

%matplotlib inline

root = os.getcwd()
root_data = root + "/grib_data"
root_URL = "grib_data/Z__C_RJTD_20180101000000_CWM_GPV_Rjp_Gll0p05deg_FD0000-0300_grib2.bin"
dataname = "Z__C_RJTD_20180101000000_CWM_GPV_Rjp_Gll0p05deg_FD0000-0300_grib2.bin"


In [2]:
grbs = pygrib.open(root_URL)

In [3]:
#check parameters in gribfile
for grb in grbs:
    print(grb)

1:Significant height of combined wind waves and swell:m (instant):regular_ll:surface:level 0:fcst time 0 hrs:from 201801010000
2:Primary wave mean period:s (instant):regular_ll:surface:level 0:fcst time 0 hrs:from 201801010000
3:Primary wave direction:Degree true (instant):regular_ll:surface:level 0:fcst time 0 hrs:from 201801010000
4:Significant height of combined wind waves and swell:m (instant):regular_ll:surface:level 0:fcst time 3 hrs:from 201801010000
5:Primary wave mean period:s (instant):regular_ll:surface:level 0:fcst time 3 hrs:from 201801010000
6:Primary wave direction:Degree true (instant):regular_ll:surface:level 0:fcst time 3 hrs:from 201801010000
7:Significant height of combined wind waves and swell:m (instant):regular_ll:surface:level 0:fcst time 6 hrs:from 201801010000
8:Primary wave mean period:s (instant):regular_ll:surface:level 0:fcst time 6 hrs:from 201801010000
9:Primary wave direction:Degree true (instant):regular_ll:surface:level 0:fcst time 6 hrs:from 20180101

In [4]:
# lats,lonsは二次元配列で緯度経度が入っている
lats, lons = grb.latlons()

#一次元に変換
# 二次元のままでは描画できない
# 2次元の格子点を1次元配列にならす
flat_lats= np.ravel(lats)
flat_lons= np.ravel(lons)

pd_all= {'lons':flat_lons, 'lats':flat_lats}

#ID 27 is Temperature:K (instant):regular_ll:heightAboveGround:level 1.5 m:fcst time 2 hrs:from 201801010000
# selectメソッドで指定した要素(forecastTime=0)にマッチする要素の配列が返ってくる。
# forecastTime=0の要素は複数あるが先頭([0])はTempratureが入っている

j = 0

for i in range(76,126,2):
    grb = grbs[i]
    # 中に含まれているデータ(temprature)を二次元のndarrayで取り出す
    U_wind = grb.values
    #華氏を摂氏に変換
    flat_U_wind= np.ravel(U_wind)
    pd_name="U_wind FH"+str(j)
    j=j+3
    pd_all[pd_name]=flat_U_wind

j = 0

for i in range(77,126,2):
    grb = grbs[i]
    print(grb)
    # 中に含まれているデータ(temprature)を二次元のndarrayで取り出す
    V_wind = grb.values
    #華氏を摂氏に変換
    flat_V_wind= np.ravel(V_wind)
    pd_name="V_wind FH"+str(j)
    j=j+3
    pd_all[pd_name]=flat_V_wind
    
df_all= pd.DataFrame(pd_all)
print(len(df_all))
df_all[:10]

77:10 metre V wind component:m s**-1 (instant):regular_ll:heightAboveGround:level 10 m:fcst time 0 hrs:from 201801010000
79:10 metre V wind component:m s**-1 (instant):regular_ll:heightAboveGround:level 10 m:fcst time 3 hrs:from 201801010000
81:10 metre V wind component:m s**-1 (instant):regular_ll:heightAboveGround:level 10 m:fcst time 6 hrs:from 201801010000
83:10 metre V wind component:m s**-1 (instant):regular_ll:heightAboveGround:level 10 m:fcst time 9 hrs:from 201801010000
85:10 metre V wind component:m s**-1 (instant):regular_ll:heightAboveGround:level 10 m:fcst time 12 hrs:from 201801010000
87:10 metre V wind component:m s**-1 (instant):regular_ll:heightAboveGround:level 10 m:fcst time 15 hrs:from 201801010000
89:10 metre V wind component:m s**-1 (instant):regular_ll:heightAboveGround:level 10 m:fcst time 18 hrs:from 201801010000
91:10 metre V wind component:m s**-1 (instant):regular_ll:heightAboveGround:level 10 m:fcst time 21 hrs:from 201801010000
93:10 metre V wind component

lons  lats  U_wind FH0  U_wind FH3  U_wind FH6  U_wind FH9  U_wind FH12  \
0  120.00  50.0    2.356874    2.508750    2.777813    2.581875     2.204376   
1  120.05  50.0    2.513124    2.641562    2.902813    2.738125     2.391876   
2  120.10  50.0    2.606874    2.727500    2.996563    2.863125     2.532501   
3  120.15  50.0    2.606874    2.743125    3.027813    2.910000     2.579376   
4  120.20  50.0    2.606874    2.750937    3.051250    2.956875     2.626251   
5  120.25  50.0    2.591249    2.750937    3.082500    2.988125     2.673126   
6  120.30  50.0    2.575624    2.758750    3.098125    3.035000     2.704376   
7  120.35  50.0    2.559999    2.750937    3.113750    3.050625     2.735626   
8  120.40  50.0    2.450624    2.641562    3.020000    3.003750     2.688751   
9  120.45  50.0    2.341249    2.540000    2.926250    2.956875     2.641876   

   U_wind FH15  U_wind FH18  U_wind FH21  ...  V_wind FH45  V_wind FH48  \
0     2.116875     2.306875     2.284376  ...     1.364063     2.029688   
1     2.304375     2.463125     2.471876  ...     1.293751     1.951563   
2     2.445000     2.603750     2.596876  ...     1.207813     1.873438   
3     2.476250     2.635000     2.628126  ...     1.121876     1.810938   
4     2.491875     2.666250     2.643751  ...     1.028126     1.740625   
5     2.507500     2.713125     2.675001  ...     0.942188     1.670313   
6     2.538750     2.744375     2.706251  ...     0.848438     1.600000   
7     2.554375     2.775625     2.706251  ...     0.762501     1.529688   
8     2.476250     2.713125     2.643751  ...     0.707813     1.482813   
9     2.413750     2.666250     2.581251  ...     0.660938     1.420313   

   V_wind FH51  V_wind FH54  V_wind FH57  V_wind FH60  V_wind FH63  \
0     1.258438     1.240625     2.483126     2.880312     2.932188   
1     1.219376     1.201563     2.428438     2.856874     2.940001   
2     1.172501     1.139063     2.373751     2.833437     2.940001   
3     1.102188     1.053125     2.287813     2.802187     2.932188   
4     1.039688     0.967188     2.209688     2.763124     2.916563   
5     0.969376     0.889063     2.131563     2.716249     2.908751   
6     0.906876     0.810938     2.053438     2.677187     2.900938   
7     0.836563     0.732813     1.967501     2.638124     2.893126   
8     0.781876     0.662500     1.889376     2.567812     2.838438   
9     0.727188     0.592188     1.819063     2.497499     2.791563   

   V_wind FH66  V_wind FH69  V_wind FH72  
0     3.058125     3.341563     3.518437  
1     3.073750     3.357188     3.549687  
2     3.073750     3.380626     3.557500  
3     3.073750     3.357188     3.549687  
4     3.058125     3.349376     3.541875  
5     3.050313     3.341563     3.526250  
6     3.042500     3.333751     3.518437  
7     3.019063     3.310313     3.502812  
8     2.972188     3.232188     3.416875  
9     2.917500     3.161876     3.330937  

[10 rows x 52 columns]

In [5]:
#緯度経度の範囲を選択
east_lon=131.69
west_lon=129.4337
north_lat=34.1413
south_lat=31.01

In [6]:
#range adjust
df=df_all[df_all['lons'] > west_lon]
df=df[df['lons'] < east_lon]

df=df[df['lats'] > south_lat]
df=df[df['lats'] < north_lat]
print(len(df))
df[:10]

2790


lons  lats  U_wind FH0  U_wind FH3  U_wind FH6  U_wind FH9  \
191307  129.45  34.1    4.513124    5.368125    4.559063    3.238125   
191308  129.50  34.1    4.794374    5.641562    4.793438    3.425625   
191309  129.55  34.1    5.075624    5.907187    5.020000    3.613125   
191310  129.60  34.1    5.372499    6.172812    5.246563    3.816250   
191311  129.65  34.1    5.450624    6.196250    5.277813    3.847500   
191312  129.70  34.1    5.528749    6.227500    5.309063    3.878750   
191313  129.75  34.1    5.606874    6.258750    5.340313    3.910000   
191314  129.80  34.1    5.684999    6.290000    5.371563    3.941250   
191315  129.85  34.1    5.747499    6.313437    5.410625    3.956875   
191316  129.90  34.1    5.794374    6.336875    5.441875    3.972500   

        U_wind FH12  U_wind FH15  U_wind FH18  U_wind FH21  ...  V_wind FH45  \
191307     2.673126     2.851250     3.416250     3.643751  ...    -7.026562   
191308     2.876251     3.054375     3.635000     3.893751  ...    -7.440624   
191309     3.095001     3.257500     3.853750     4.159376  ...    -7.846874   
191310     3.298126     3.476250     4.072500     4.409376  ...    -8.260937   
191311     3.376251     3.538750     4.135000     4.503126  ...    -8.307812   
191312     3.470001     3.616875     4.197500     4.596876  ...    -8.370312   
191313     3.548126     3.679375     4.260000     4.690626  ...    -8.417187   
191314     3.641876     3.757500     4.322500     4.784376  ...    -8.479687   
191315     3.704376     3.804375     4.369375     4.846876  ...    -8.503124   
191316     3.766876     3.866875     4.416250     4.925001  ...    -8.518749   

        V_wind FH48  V_wind FH51  V_wind FH54  V_wind FH57  V_wind FH60  \
191307    -6.259375    -5.491562    -5.220312    -5.298124    -4.963438   
191308    -6.587500    -5.757187    -5.446875    -5.532499    -5.158751   
191309    -6.923437    -6.030624    -5.673437    -5.759062    -5.361876   
191310    -7.251562    -6.311874    -5.900000    -5.993437    -5.557188   
191311    -7.282812    -6.343124    -5.923437    -5.977812    -5.533751   
191312    -7.306250    -6.382187    -5.931250    -5.969999    -5.502501   
191313    -7.337500    -6.413437    -5.946875    -5.962187    -5.471251   
191314    -7.368750    -6.452499    -5.962500    -5.946562    -5.432188   
191315    -7.392187    -6.483749    -5.993750    -5.962187    -5.416563   
191316    -7.407812    -6.522812    -6.009375    -5.969999    -5.400938   

        V_wind FH63  V_wind FH66  V_wind FH69  V_wind FH72  
191307    -4.927187    -4.512187    -4.330312    -4.067500  
191308    -5.153749    -4.730937    -4.549062    -4.262813  
191309    -5.356874    -4.949687    -4.759999    -4.458125  
191310    -5.583437    -5.168437    -4.970937    -4.661250  
191311    -5.552187    -5.168437    -4.978749    -4.669063  
191312    -5.528749    -5.168437    -4.986562    -4.669063  
191313    -5.497499    -5.168437    -5.002187    -4.676875  
191314    -5.481874    -5.168437    -5.009999    -4.692500  
191315    -5.450624    -5.152812    -4.986562    -4.661250  
191316    -5.411562    -5.121562    -4.970937    -4.630000  

[10 rows x 52 columns]

In [7]:
map_lat=df['lats'].values
map_lon=df['lons'].values
FH0=np.round(df['U_wind FH0'].values,2)
FH1=np.round(df['U_wind FH3'].values,2)
FH2=np.round(df['U_wind FH6'].values,2)
FH3=np.round(df['U_wind FH9'].values,2)
FH4=np.round(df['U_wind FH12'].values,2)
FH5=np.round(df['U_wind FH15'].values,2)

In [8]:
from folium import plugins

#lat-long of focus area and zoom start
map = folium.Map([33.518022,130.471583], zoom_start=12)

# Mapbox makes some nice map tiles,
# Stamen also produce some cool map tiles which typically work at all zoom levels.
tile = folium.TileLayer('Stamen Terrain').add_to(map)

#adding marker and popup of temperature
for i in range(0,len(map_lat)):
    
    icon_number = plugins.BeautifyIcon(
    border_color='#00ABDC',
    text_color='#00ABDC',
    border_width=2,
    number=str(int(FH0[i])),
    inner_icon_style='margin-top:0;')
    
    folium.Marker(location=[float(map_lat[i])  ,float(map_lon[i])],\
                  popup="___U_wind___"+"\n"\
                          +"__FH0= "+str(FH0[i])+"__\n"\
                          +"__FH1 = "+str(FH1[i])+"__\n"\
                          +"__FH2 = "+str(FH2[i])+"__\n"\
                          +"__FH3 = "+str(FH3[i])+"__\n"\
                          +"__FH4 = "+str(FH4[i])+"__\n"\
                          +"__FH5 = "+str(FH5[i])+"__\n",\
                 icon=icon_number).add_to(map)
    
#we can change tiles with help of LayerConrol
folium.LayerControl().add_to(map)

#Adding mouse position
formatter = "function(num) {return L.Util.formatNum(num, 3) + ' º ';};"

folium.plugins.MousePosition(
    position='topright',
    separator=' | ',
    empty_string='NaN',
    lng_first=True,
    num_digits=20,
    prefix='Coordinates:',
    lat_formatter=formatter,
    lng_formatter=formatter
).add_to(map)

map_name="Output_MAP/"+"FH_U_wind_Map_" + year + "_" + month + "_" + day+".html"

map.save(outfile=map_name)

map

In [9]:
elapsed_time = time.time() - start

print("elapsed_time:{0}".format(elapsed_time))

elapsed_time:19.778173685073853


## Problem
### If we try to get only one package of forcasting data from the web site, it spend much time. So, how to calculate or predict output of electricity with numerous data is a problem. My machine take alot of time.